### 映射关系
以单跳查询(Q10002,timeZone):Q207020为例</br>
首先进行实体映射，结果为e_dict，e_dict["<http://wikidata.dbpedia.org/resource/Q10002>"]=9537</br>
然后进行关系映射，结果为r_dict，r_dict[<http://wikidata.dbpedia.org/ontology/timeZone>]=220</br>
filters_e[(9537,220)] = [23355]

In [3]:
data = load_obj('../data/DBpedia/input/1p.pkl')

In [11]:
list_of_items = [(key, value) for key, value in data["test"]["c"].items()]
list_of_items[-200:]

[(('<http://wikidata.dbpedia.org/resource/Q963038>',
   '<http://wikidata.dbpedia.org/ontology/country>'),
  {'<http://schema.org/Country>',
   '<http://schema.org/Place>',
   '<http://wikidata.dbpedia.org/ontology/Location>',
   '<http://wikidata.dbpedia.org/ontology/Place>',
   '<http://wikidata.dbpedia.org/ontology/PopulatedPlace>',
   '<http://www.w3.org/2002/07/owl#Thing>',
   '<http://www.wikidata.org/entity/Q6256>'}),
 (('<http://wikidata.dbpedia.org/resource/Q963038>',
   '<http://wikidata.dbpedia.org/ontology/isPartOf>'),
  {'<http://wikidata.dbpedia.org/ontology/Place>'}),
 (('<http://wikidata.dbpedia.org/resource/Q963044>',
   '<http://wikidata.dbpedia.org/ontology/associatedBand>'),
  {'<http://www.wikidata.org/entity/Q215380>'}),
 (('<http://wikidata.dbpedia.org/resource/Q963044>',
   '<http://wikidata.dbpedia.org/ontology/birthPlace>'),
  {'<http://schema.org/AdministrativeArea>', '<http://schema.org/Place>'}),
 (('<http://wikidata.dbpedia.org/resource/Q963044>',
   '<htt

In [ ]:
len(data["test"]["e"].keys())

In [ ]:
for k in data["test"]["e"].keys():
    print(k)
    print(data["test"]["e"][k])
    print(data["test_filter"]["e"][k])
    print( )
#     print(data["test"]["e"][k] == data["test_filter"]["e"][k])
# len(data["test"]["e"])
# len(data["test_filter"]["e"])

In [5]:
e_dict["<http://wikidata.dbpedia.org/resource/Q10002>"]
r_dict["<http://wikidata.dbpedia.org/ontology/timeZone>"]
filters_e[(22773, 270)]
e_dict["<http://wikidata.dbpedia.org/resource/Q207020>"]

NameError: name 'filters_e' is not defined

In [1]:
import torch 
import pandas as pd
import pdb
import argparse
import pickle
import os
import numpy as np
import random
import tqdm
import time
from TAR import *
from my import *
from utils import *
from graph import *

In [4]:
# save_root = '../models/initial//'
# model_path = save_root + str(900)
save_root = '../models/13/'
model_path = save_root + str(800)
dataset = "DBpedia"
cfg = parse_args(["--dataset",dataset])
seed_everything(cfg.seed)
device = torch.device(f'cuda:{cfg.gpu}' if torch.cuda.is_available() else 'cpu')
e_dict, c_dict, r_dict, ot, is_data_train = get_mapper(cfg.root + cfg.dataset + '/')

model = TAR(cfg.emb_dim, e_dict, c_dict, r_dict)
model.load_state_dict(torch.load(model_path))

edges = build_edges_incomplete(e_dict, r_dict, dataset)
nodes = build_nodes(e_dict, dataset)
graph = build_graph(nodes, edges)

E: 0--28523, C: 0--976, R: 326


RuntimeError: The expanded size of the tensor (256) must match the existing size (768) at non-singleton dimension 0.  Target sizes: [256].  Tensor sizes: [768]

### 平均度数计算

In [3]:
degrees = list(dict(graph.degree()).values())
p25, p50, p75 = np.percentile(degrees, [75, 85, 99])
print("25% percentile:", p25)
print("50% percentile:", p50)
print("75% percentile:", p75)

25% percentile: 9.0
50% percentile: 13.0
75% percentile: 61.0


In [28]:
# graph[28104]
graph.in_edges(28104)

InEdgeDataView([(9747, 28104), (16280, 28104), (27042, 28104), (27966, 28104)])

In [32]:
print(get_e_by_dict(e_dict,9747))
print(get_e_by_dict(e_dict,16280))
print(get_e_by_dict(e_dict,27042))
print(get_e_by_dict(e_dict,27966))

<http://wikidata.dbpedia.org/resource/Q20800404>
<http://wikidata.dbpedia.org/resource/Q37227>
<http://wikidata.dbpedia.org/resource/Q866>
<http://wikidata.dbpedia.org/resource/Q94>


In [15]:
my_dict = dict(graph.degree())
sorted_dict = sorted(my_dict.items(), key=lambda x: x[1], reverse=True)
# 计算排名前 1% 的数量
top_1_percent = int(len(sorted_dict) * 0.01)
# 获取排名前 1% 的键
top_keys = [key for key, _ in sorted_dict[:top_1_percent]]
for k in top_keys:
    print(get_e_by_dict(e_dict, k))

<http://wikidata.dbpedia.org/resource/Q30>
<http://wikidata.dbpedia.org/resource/Q729>
<http://wikidata.dbpedia.org/resource/Q99>
<http://wikidata.dbpedia.org/resource/Q145>
<http://wikidata.dbpedia.org/resource/Q25989>
<http://wikidata.dbpedia.org/resource/Q794>
<http://wikidata.dbpedia.org/resource/Q11366>
<http://wikidata.dbpedia.org/resource/Q207020>
<http://wikidata.dbpedia.org/resource/Q11401>
<http://wikidata.dbpedia.org/resource/Q37073>
<http://wikidata.dbpedia.org/resource/Q36>
<http://wikidata.dbpedia.org/resource/Q1360>
<http://wikidata.dbpedia.org/resource/Q21>
<http://wikidata.dbpedia.org/resource/Q11399>
<http://wikidata.dbpedia.org/resource/Q1390>
<http://wikidata.dbpedia.org/resource/Q60>
<http://wikidata.dbpedia.org/resource/Q6607>
<http://wikidata.dbpedia.org/resource/Q183945>
<http://wikidata.dbpedia.org/resource/Q16>
<http://wikidata.dbpedia.org/resource/Q84>
<http://wikidata.dbpedia.org/resource/Q668>
<http://wikidata.dbpedia.org/resource/Q83270>
<http://wikidata.d

In [4]:
train_e_1p, train_c_1p, train_filter_e_1p, train_filter_c_1p, test_e_1p, test_c_1p, test_filter_e_1p, test_filter_c_1p, valid_dataloader_1p_e, valid_dataloader_1p_c, test_dataloader_1p_e, test_dataloader_1p_c = load_train_and_test_data(cfg.root + cfg.dataset + '/', cfg.num_workers, e_dict, c_dict, r_dict, query_type='1p')
train_e_2p, train_c_2p, train_filter_e_2p, train_filter_c_2p, test_e_2p, test_c_2p, test_filter_e_2p, test_filter_c_2p, valid_dataloader_2p_e, valid_dataloader_2p_c, test_dataloader_2p_e, test_dataloader_2p_c = load_train_and_test_data(cfg.root + cfg.dataset + '/', cfg.num_workers, e_dict, c_dict, r_dict, query_type='2p')
train_e_3p, train_c_3p, train_filter_e_3p, train_filter_c_3p, test_e_3p, test_c_3p, test_filter_e_3p, test_filter_c_3p, valid_dataloader_3p_e, valid_dataloader_3p_c, test_dataloader_3p_e, test_dataloader_3p_c = load_train_and_test_data(cfg.root + cfg.dataset + '/', cfg.num_workers, e_dict, c_dict, r_dict, query_type='3p')
train_e_2i, train_c_2i, train_filter_e_2i, train_filter_c_2i, test_e_2i, test_c_2i, test_filter_e_2i, test_filter_c_2i, valid_dataloader_2i_e, valid_dataloader_2i_c, test_dataloader_2i_e, test_dataloader_2i_c = load_train_and_test_data(cfg.root + cfg.dataset + '/', cfg.num_workers, e_dict, c_dict, r_dict, query_type='2i')
train_e_3i, train_c_3i, train_filter_e_3i, train_filter_c_3i, test_e_3i, test_c_3i, test_filter_e_3i, test_filter_c_3i, valid_dataloader_3i_e, valid_dataloader_3i_c, test_dataloader_3i_e, test_dataloader_3i_c = load_train_and_test_data(cfg.root + cfg.dataset + '/', cfg.num_workers, e_dict, c_dict, r_dict, query_type='3i')
test_e_pi, test_c_pi, test_filter_e_pi, test_filter_c_pi, valid_dataloader_pi_e, valid_dataloader_pi_c, test_dataloader_pi_e, test_dataloader_pi_c = load_test_data(cfg.root + cfg.dataset + '/', cfg.num_workers, e_dict, c_dict, r_dict, query_type='pi')
test_e_ip, test_c_ip, test_filter_e_ip, test_filter_c_ip, valid_dataloader_ip_e, valid_dataloader_ip_c, test_dataloader_ip_e, test_dataloader_ip_c = load_test_data(cfg.root + cfg.dataset + '/', cfg.num_workers, e_dict, c_dict, r_dict, query_type='ip')
test_e_2u, test_c_2u, test_filter_e_2u, test_filter_c_2u, valid_dataloader_2u_e, valid_dataloader_2u_c, test_dataloader_2u_e, test_dataloader_2u_c = load_test_data(cfg.root + cfg.dataset + '/', cfg.num_workers, e_dict, c_dict, r_dict, query_type='2u')
test_e_up, test_c_up, test_filter_e_up, test_filter_c_up, valid_dataloader_up_e, valid_dataloader_up_c, test_dataloader_up_e, test_dataloader_up_c = load_test_data(cfg.root + cfg.dataset + '/', cfg.num_workers, e_dict, c_dict, r_dict, query_type='up')

In [4]:
for i in train_e_1p:
    print(i)

tensor([   11,     0,     0,     0,     0,     0,    61, 21532])
tensor([  11,    0,    0,    0,    0,    0,  113, 6717])
tensor([   11,     0,     0,     0,     0,     0,   137, 25625])
tensor([  11,    0,    0,    0,    0,    0,  307, 9642])
tensor([   11,     0,     0,     0,     0,     0,   307, 12344])
tensor([   11,     0,     0,     0,     0,     1,    61, 14098])
tensor([  11,    0,    0,    0,    0,    1,  137, 1653])
tensor([  11,    0,    0,    0,    0,    1,  137, 1780])
tensor([   11,     0,     0,     0,     0,     2,    61, 21532])
tensor([  11,    0,    0,    0,    0,    2,  113, 6717])
tensor([   11,     0,     0,     0,     0,     2,   137, 25625])
tensor([   11,     0,     0,     0,     0,     2,   152, 25151])
tensor([  11,    0,    0,    0,    0,    2,  307, 9642])
tensor([  11,    0,    0,    0,    0,    3,   16, 6716])
tensor([  11,    0,    0,    0,    0,    3,   17, 6716])
tensor([  11,    0,    0,    0,    0,    3,  111, 9685])
tensor([   11,     0,     0,    

tensor([  11,    0,    0,    0,    0, 1007,  295, 4859])
tensor([   11,     0,     0,     0,     0,  1009,   111, 16222])
tensor([  11,    0,    0,    0,    0, 1009,  111, 1463])
tensor([   11,     0,     0,     0,     0,  1009,   111, 28240])
tensor([  11,    0,    0,    0,    0, 1009,  249, 9978])
tensor([  11,    0,    0,    0,    0, 1009,  249, 9067])
tensor([   11,     0,     0,     0,     0,  1010,   120, 13795])
tensor([   11,     0,     0,     0,     0,  1010,   120, 21744])
tensor([  11,    0,    0,    0,    0, 1012,  111, 3975])
tensor([   11,     0,     0,     0,     0,  1012,   111, 22507])
tensor([   11,     0,     0,     0,     0,  1012,   111, 26476])
tensor([   11,     0,     0,     0,     0,  1012,   126, 19368])
tensor([   11,     0,     0,     0,     0,  1012,   249, 26098])
tensor([  11,    0,    0,    0,    0, 1012,  249,  370])
tensor([   11,     0,     0,     0,     0,  1012,   249, 10388])
tensor([   11,     0,     0,     0,     0,  1012,   249, 24446])
tensor([

tensor([   11,     0,     0,     0,     0,  1876,   137, 19696])
tensor([   11,     0,     0,     0,     0,  1876,   307, 27849])
tensor([   11,     0,     0,     0,     0,  1877,    61, 14098])
tensor([   11,     0,     0,     0,     0,  1877,   137, 19699])
tensor([  11,    0,    0,    0,    0, 1877,  137, 4214])
tensor([  11,    0,    0,    0,    0, 1877,  323, 4214])
tensor([  11,    0,    0,    0,    0, 1878,   61, 5422])
tensor([   11,     0,     0,     0,     0,  1878,   124, 13306])
tensor([  11,    0,    0,    0,    0, 1878,  128,  453])
tensor([   11,     0,     0,     0,     0,  1878,   128, 22639])
tensor([  11,    0,    0,    0,    0, 1878,  136, 2694])
tensor([   11,     0,     0,     0,     0,  1878,   136, 26986])
tensor([   11,     0,     0,     0,     0,  1879,   251, 16434])
tensor([  11,    0,    0,    0,    0, 1879,  295, 4214])
tensor([   11,     0,     0,     0,     0,  1880,     2, 21490])
tensor([   11,     0,     0,     0,     0,  1880,    18, 13297])
tensor([

tensor([  11,    0,    0,    0,    0, 2864,  137, 6288])
tensor([   11,     0,     0,     0,     0,  2864,   217, 23031])
tensor([   11,     0,     0,     0,     0,  2864,   217, 19993])
tensor([   11,     0,     0,     0,     0,  2864,   307, 11594])
tensor([   11,     0,     0,     0,     0,  2865,    22, 16009])
tensor([  11,    0,    0,    0,    0, 2865,   22,  962])
tensor([   11,     0,     0,     0,     0,  2865,    61, 24787])
tensor([   11,     0,     0,     0,     0,  2865,   177, 24117])
tensor([   11,     0,     0,     0,     0,  2865,   177, 12223])
tensor([  11,    0,    0,    0,    0, 2865,  177, 5042])
tensor([   11,     0,     0,     0,     0,  2865,   199, 18518])
tensor([   11,     0,     0,     0,     0,  2865,   220, 15689])
tensor([   11,     0,     0,     0,     0,  2866,    61, 25932])
tensor([  11,    0,    0,    0,    0, 2866,  137, 6782])
tensor([   11,     0,     0,     0,     0,  2866,   217, 18492])
tensor([   11,     0,     0,     0,     0,  2866,   307, 

tensor([   11,     0,     0,     0,     0,  3802,    27, 10815])
tensor([   11,     0,     0,     0,     0,  3802,    70, 11242])
tensor([  11,    0,    0,    0,    0, 3803,   81, 7083])
tensor([   11,     0,     0,     0,     0,  3803,   143, 25458])
tensor([   11,     0,     0,     0,     0,  3804,    16, 15176])
tensor([  11,    0,    0,    0,    0, 3804,   16, 8658])
tensor([   11,     0,     0,     0,     0,  3804,    16, 14062])
tensor([  11,    0,    0,    0,    0, 3804,   16, 3604])
tensor([   11,     0,     0,     0,     0,  3804,    17, 15176])
tensor([  11,    0,    0,    0,    0, 3804,   17, 8658])
tensor([   11,     0,     0,     0,     0,  3804,    17, 14062])
tensor([  11,    0,    0,    0,    0, 3804,   17, 3604])
tensor([   11,     0,     0,     0,     0,  3804,    21, 20319])
tensor([   11,     0,     0,     0,     0,  3804,   111, 18777])
tensor([   11,     0,     0,     0,     0,  3804,   126, 19092])
tensor([   11,     0,     0,     0,     0,  3804,   126, 14098])


...

tensor([   11,     0,     0,     0,     0, 20373,   249, 21043])
tensor([   11,     0,     0,     0,     0, 20373,   324, 27608])
tensor([   11,     0,     0,     0,     0, 20376,    27, 14098])
tensor([   11,     0,     0,     0,     0, 20376,   127, 24066])
tensor([   11,     0,     0,     0,     0, 20376,   203, 26731])
tensor([   11,     0,     0,     0,     0, 20376,   247, 25754])
tensor([   11,     0,     0,     0,     0, 20376,   247, 21065])
tensor([   11,     0,     0,     0,     0, 20376,   247, 23098])
tensor([   11,     0,     0,     0,     0, 20376,   247, 23166])
tensor([   11,     0,     0,     0,     0, 20376,   247, 25372])
tensor([   11,     0,     0,     0,     0, 20376,   247, 25034])
tensor([   11,     0,     0,     0,     0, 20376,   247, 20418])
tensor([   11,     0,     0,     0,     0, 20376,   247, 23755])
tensor([   11,     0,     0,     0,     0, 20376,   247, 19376])
tensor([   11,     0,     0,     0,     0, 20376,   247, 18560])
tensor([   11,     0,    

tensor([   11,     0,     0,     0,     0, 21024,   148, 24923])
tensor([   11,     0,     0,     0,     0, 21024,   295, 25696])
tensor([   11,     0,     0,     0,     0, 21024,   323, 23321])
tensor([   11,     0,     0,     0,     0, 21025,    61, 14098])
tensor([   11,     0,     0,     0,     0, 21025,   295, 25696])
tensor([   11,     0,     0,     0,     0, 21025,   323, 23321])
tensor([   11,     0,     0,     0,     0, 21026,   100, 15766])
tensor([   11,     0,     0,     0,     0, 21026,   111, 22507])
tensor([   11,     0,     0,     0,     0, 21026,   111, 10886])
tensor([   11,     0,     0,     0,     0, 21026,   111,  5275])
tensor([   11,     0,     0,     0,     0, 21026,   111, 10223])
tensor([   11,     0,     0,     0,     0, 21026,   111,  8107])
tensor([   11,     0,     0,     0,     0, 21026,   111, 26513])
tensor([   11,     0,     0,     0,     0, 21026,   126, 14098])
tensor([   11,     0,     0,     0,     0, 21026,   126,  6436])
tensor([   11,     0,    

tensor([   11,     0,     0,     0,     0, 21829,   111, 26513])
tensor([   11,     0,     0,     0,     0, 21829,   203, 25244])
tensor([   11,     0,     0,     0,     0, 21830,   219, 26703])
tensor([   11,     0,     0,     0,     0, 21830,   257, 18467])
tensor([   11,     0,     0,     0,     0, 21830,   323, 10721])
tensor([   11,     0,     0,     0,     0, 21831,    61, 14098])
tensor([   11,     0,     0,     0,     0, 21831,   137,   943])
tensor([   11,     0,     0,     0,     0, 21831,   137,  2075])
tensor([   11,     0,     0,     0,     0, 21832,   120,  4977])
tensor([   11,     0,     0,     0,     0, 21832,   153, 25225])
tensor([   11,     0,     0,     0,     0, 21832,   231, 15799])
tensor([   11,     0,     0,     0,     0, 21833,     6, 19603])
tensor([   11,     0,     0,     0,     0, 21833,    27,  7276])
tensor([   11,     0,     0,     0,     0, 21833,    27,  5051])
tensor([   11,     0,     0,     0,     0, 21833,   232, 21836])
tensor([   11,     0,    

tensor([   11,     0,     0,     0,     0, 22738,   111, 16700])
tensor([   11,     0,     0,     0,     0, 22738,   111,  7840])
tensor([   11,     0,     0,     0,     0, 22738,   111, 26476])
tensor([   11,     0,     0,     0,     0, 22738,   126,  4197])
tensor([   11,     0,     0,     0,     0, 22738,   249,  9160])
tensor([   11,     0,     0,     0,     0, 22738,   249,   256])
tensor([   11,     0,     0,     0,     0, 22739,     2, 21490])
tensor([   11,     0,     0,     0,     0, 22739,    18, 13297])
tensor([   11,     0,     0,     0,     0, 22739,    35, 24126])
tensor([   11,     0,     0,     0,     0, 22739,    50, 13238])
tensor([   11,     0,     0,     0,     0, 22739,   295,  5766])
tensor([   11,     0,     0,     0,     0, 22740,    61,  4601])
tensor([   11,     0,     0,     0,     0, 22740,   215, 25089])
tensor([   11,     0,     0,     0,     0, 22740,   215, 16743])
tensor([   11,     0,     0,     0,     0, 22741,    64, 23588])
tensor([   11,     0,    

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [5]:
print(graph[23139])
print(get_e_by_dict(r_dict, 323))
print(get_e_by_dict(r_dict, 31))
print(graph[24154])
# r_dict

{12898: {'relation': '<http://wikidata.dbpedia.org/ontology/associatedMusicalArtist>', 'r_dict': 17}, 24777: {'relation': '<http://wikidata.dbpedia.org/ontology/bandMember>', 'r_dict': 21}, 28319: {'relation': '<http://wikidata.dbpedia.org/ontology/formerBandMember>', 'r_dict': 100}, 11459: {'relation': '<http://wikidata.dbpedia.org/ontology/genre>', 'r_dict': 111}}
<http://www.w3.org/2000/01/rdf-schema#seeAlso>
<http://wikidata.dbpedia.org/ontology/borough>
{6082: {'relation': '<http://wikidata.dbpedia.org/ontology/associatedMusicalArtist>', 'r_dict': 17}, 22446: {'relation': '<http://wikidata.dbpedia.org/ontology/birthPlace>', 'r_dict': 27}, 11173: {'relation': '<http://wikidata.dbpedia.org/ontology/deathPlace>', 'r_dict': 70}, 10223: {'relation': '<http://wikidata.dbpedia.org/ontology/genre>', 'r_dict': 111}, 11459: {'relation': '<http://wikidata.dbpedia.org/ontology/genre>', 'r_dict': 111}, 26513: {'relation': '<http://wikidata.dbpedia.org/ontology/genre>', 'r_dict': 111}, 12320: {

In [5]:
train_filter_e_1p[(18868, 137)]

[28523, 827]

In [8]:
train_filters_e = {'1p': train_filter_e_1p, '2p': train_filter_e_2p, '3p': train_filter_e_3p}
train_filters_c = {'1p': train_filter_c_1p, '2p': train_filter_c_2p, '3p': train_filter_c_3p}
train_dataset = ValidDataset(train_e_1p, len(e_dict))
train_dataloader = torch.utils.data.DataLoader(dataset=train_dataset, batch_size=1, num_workers=1, shuffle=False, drop_last=False)
# test
loader = valid_dataloader_2i_e
filters_e = test_filter_e_2i
gt = get_dict_gt(e_dict, r_dict, '2i')
# train
# loader = train_dataloader
# filters_e = train_filter_e_1p

In [3]:
train_ot = ppc(ot, e_dict, c_dict, r_dict, query_type='ot', answer_type=None, flag=None)
train_is = ppc(is_data_train, e_dict, c_dict, r_dict, query_type='is', answer_type=None, flag=None)

train_e_1p, train_c_1p, train_filter_e_1p, train_filter_c_1p, test_e_1p, test_c_1p, test_filter_e_1p, test_filter_c_1p, valid_dataloader_1p_e, valid_dataloader_1p_c, test_dataloader_1p_e, test_dataloader_1p_c = load_train_and_test_data(cfg.root + cfg.dataset + '/', cfg.num_workers, e_dict, c_dict, r_dict, query_type='1p')
train_e_2p, train_c_2p, train_filter_e_2p, train_filter_c_2p, test_e_2p, test_c_2p, test_filter_e_2p, test_filter_c_2p, valid_dataloader_2p_e, valid_dataloader_2p_c, test_dataloader_2p_e, test_dataloader_2p_c = load_train_and_test_data(cfg.root + cfg.dataset + '/', cfg.num_workers, e_dict, c_dict, r_dict, query_type='2p')
train_e_3p, train_c_3p, train_filter_e_3p, train_filter_c_3p, test_e_3p, test_c_3p, test_filter_e_3p, test_filter_c_3p, valid_dataloader_3p_e, valid_dataloader_3p_c, test_dataloader_3p_e, test_dataloader_3p_c = load_train_and_test_data(cfg.root + cfg.dataset + '/', cfg.num_workers, e_dict, c_dict, r_dict, query_type='3p')
train_e_2i, train_c_2i, train_filter_e_2i, train_filter_c_2i, test_e_2i, test_c_2i, test_filter_e_2i, test_filter_c_2i, valid_dataloader_2i_e, valid_dataloader_2i_c, test_dataloader_2i_e, test_dataloader_2i_c = load_train_and_test_data(cfg.root + cfg.dataset + '/', cfg.num_workers, e_dict, c_dict, r_dict, query_type='2i')
train_e_3i, train_c_3i, train_filter_e_3i, train_filter_c_3i, test_e_3i, test_c_3i, test_filter_e_3i, test_filter_c_3i, valid_dataloader_3i_e, valid_dataloader_3i_c, test_dataloader_3i_e, test_dataloader_3i_c = load_train_and_test_data(cfg.root + cfg.dataset + '/', cfg.num_workers, e_dict, c_dict, r_dict, query_type='3i')
test_e_pi, test_c_pi, test_filter_e_pi, test_filter_c_pi, valid_dataloader_pi_e, valid_dataloader_pi_c, test_dataloader_pi_e, test_dataloader_pi_c = load_test_data(cfg.root + cfg.dataset + '/', cfg.num_workers, e_dict, c_dict, r_dict, query_type='pi')
test_e_ip, test_c_ip, test_filter_e_ip, test_filter_c_ip, valid_dataloader_ip_e, valid_dataloader_ip_c, test_dataloader_ip_e, test_dataloader_ip_c = load_test_data(cfg.root + cfg.dataset + '/', cfg.num_workers, e_dict, c_dict, r_dict, query_type='ip')
test_e_2u, test_c_2u, test_filter_e_2u, test_filter_c_2u, valid_dataloader_2u_e, valid_dataloader_2u_c, test_dataloader_2u_e, test_dataloader_2u_c = load_test_data(cfg.root + cfg.dataset + '/', cfg.num_workers, e_dict, c_dict, r_dict, query_type='2u')
test_e_up, test_c_up, test_filter_e_up, test_filter_c_up, valid_dataloader_up_e, valid_dataloader_up_c, test_dataloader_up_e, test_dataloader_up_c = load_test_data(cfg.root + cfg.dataset + '/', cfg.num_workers, e_dict, c_dict, r_dict, query_type='up')

train_data = torch.cat([train_ot, train_is, train_e_1p, train_c_1p, train_e_2p, train_c_2p, train_e_3p, train_c_3p, train_e_2i, train_c_2i, train_e_3i, train_c_3i], dim=0)
train_filters_e = {'1p': train_filter_e_1p, '2p': train_filter_e_2p, '3p': train_filter_e_3p, '2i': train_filter_e_2i, '3i': train_filter_e_3i}
train_filters_c = {'1p': train_filter_c_1p, '2p': train_filter_c_2p, '3p': train_filter_c_3p, '2i': train_filter_c_2i, '3i': train_filter_c_3i}
train_dataset = TrainDataset(e_dict, c_dict, train_data, num_ng=cfg.num_ng, filters={'e': train_filters_e, 'c': train_filters_c})
train_dataloader = torch.utils.data.DataLoader(dataset=train_dataset, batch_size=cfg.bs, num_workers=cfg.num_workers, shuffle=True, drop_last=True)

In [4]:
device="cpu"
model.to(device)
model.eval()
print('Validating Entity Answering:')
# _, rr_1p_e, h1_1p_e, h3_1p_e, h10_1p_e, h50_1p_e = evaluate_e(model, valid_dataloader_1p_e,
#                                                               test_filter_e_1p, device, query_type='1p')
# _, rr_2p_e, h1_2p_e, h3_2p_e, h10_2p_e, h50_2p_e = evaluate_e(model, valid_dataloader_2p_e,
#                                                               test_filter_e_2p, device, query_type='2p')
# _, rr_3p_e, h1_3p_e, h3_3p_e, h10_3p_e, h50_3p_e = evaluate_e(model, valid_dataloader_3p_e,
#                                                               test_filter_e_3p, device, query_type='3p')
# _, rr_2i_e, h1_2i_e, h3_2i_e, h10_2i_e, h50_2i_e = evaluate_e(model, valid_dataloader_2i_e,
#                                                               test_filter_e_2i, device, query_type='2i')
# _, rr_3i_e, h1_3i_e, h3_3i_e, h10_3i_e, h50_3i_e = evaluate_e(model, valid_dataloader_3i_e,
#                                                               test_filter_e_3i, device, query_type='3i')
_, rr_pi_e, h1_pi_e, h3_pi_e, h10_pi_e, h50_pi_e = evaluate_e(model, valid_dataloader_pi_e,
                                                              test_filter_e_pi, device, query_type='pi')
_, rr_ip_e, h1_ip_e, h3_ip_e, h10_ip_e, h50_ip_e = evaluate_e(model, valid_dataloader_ip_e,
                                                              test_filter_e_ip, device, query_type='ip')
_, rr_2u_e, h1_2u_e, h3_2u_e, h10_2u_e, h50_2u_e = evaluate_e(model, valid_dataloader_2u_e,
                                                              test_filter_e_2u, device, query_type='2u')
_, rr_up_e, h1_up_e, h3_up_e, h10_up_e, h50_up_e = evaluate_e(model, valid_dataloader_up_e,
                                                              test_filter_e_up, device, query_type='up')
mrr_e = round(sum([rr_1p_e, rr_2p_e, rr_3p_e, rr_2i_e, rr_3i_e, rr_pi_e, rr_ip_e, rr_2u_e, rr_up_e]) / 9, 3)
mh1_e = round(sum([h1_1p_e, h1_2p_e, h1_3p_e, h1_2i_e, h1_3i_e, h1_pi_e, h1_ip_e, h1_2u_e, h1_up_e]) / 9, 3)
mh3_e = round(sum([h3_1p_e, h3_2p_e, h3_3p_e, h3_2i_e, h3_3i_e, h3_pi_e, h3_ip_e, h3_2u_e, h3_up_e]) / 9, 3)
mh10_e = round(
    sum([h10_1p_e, h10_2p_e, h10_3p_e, h10_2i_e, h10_3i_e, h10_pi_e, h10_ip_e, h10_2u_e, h10_up_e]) / 9, 3)
mh50_e = round(
    sum([h50_1p_e, h50_2p_e, h50_3p_e, h50_2i_e, h50_3i_e, h50_pi_e, h50_ip_e, h50_2u_e, h50_up_e]) / 9, 3)
print(f'Entity Answering Mean: \n MRR: {mrr_e}, H1: {mh1_e}, H3: {mh3_e}, H10: {mh10_e}, H50: {mh50_e}')

Validating Entity Answering:
#Entity#pi# MRR: 0.387, H1: 0.243, H3: 0.448, H10: 0.675, H50: 0.914
#Entity#ip# MRR: 0.317, H1: 0.196, H3: 0.368, H10: 0.569, H50: 0.818
#Entity#2u# MRR: 0.115, H1: 0.061, H3: 0.123, H10: 0.23, H50: 0.34
#Entity#up# MRR: 0.179, H1: 0.104, H3: 0.193, H10: 0.339, H50: 0.556


NameError: name 'rr_1p_e' is not defined

In [13]:
train_ot[:100]

tensor([[  0,   0,   0,   0,   0,   0,  71, 654],
        [  0,   0,   0,   0,   0,   0,  71, 487],
        [  0,   0,   0,   0,   0,   0,  71,   8],
        [  0,   0,   0,   0,   0,   0,  71, 874],
        [  0,   0,   0,   0,   0,   0, 464, 247],
        [  0,   0,   0,   0,   0,   0, 464, 874],
        [  0,   0,   0,   0,   0,   0, 543, 299],
        [  0,   0,   0,   0,   0,   0, 543,   6],
        [  0,   0,   0,   0,   0,   0, 543, 570],
        [  0,   0,   0,   0,   0,   0, 543, 524],
        [  0,   0,   0,   0,   0,   0, 543, 506],
        [  0,   0,   0,   0,   0,   0, 543, 874],
        [  0,   0,   0,   0,   0,   0, 386, 181],
        [  0,   0,   0,   0,   0,   0, 386, 465],
        [  0,   0,   0,   0,   0,   0, 386, 506],
        [  0,   0,   0,   0,   0,   0, 386, 874],
        [  0,   0,   0,   0,   0,   0, 432, 656],
        [  0,   0,   0,   0,   0,   0, 432, 874],
        [  0,   0,   0,   0,   0,   0, 409, 500],
        [  0,   0,   0,   0,   0,   0, 409,   8],


In [21]:
train_is[:100]

tensor([[100,   0,   0,   0,   0,   0,   0, 766],
        [100,   0,   0,   0,   0,   0,   0, 783],
        [100,   0,   0,   0,   0,   0,   0, 825],
        [100,   0,   0,   0,   0,   0,   0, 836],
        [100,   0,   0,   0,   0,   0,   0, 839],
        [100,   0,   0,   0,   0,   0,   0, 846],
        [100,   0,   0,   0,   0,   0,   0, 874],
        [100,   0,   0,   0,   0,   0,   0, 949],
        [100,   0,   0,   0,   0,   0,   0, 951],
        [100,   0,   0,   0,   0,   0,   1, 783],
        [100,   0,   0,   0,   0,   0,   1, 825],
        [100,   0,   0,   0,   0,   0,   1, 836],
        [100,   0,   0,   0,   0,   0,   1, 839],
        [100,   0,   0,   0,   0,   0,   1, 846],
        [100,   0,   0,   0,   0,   0,   1, 874],
        [100,   0,   0,   0,   0,   0,   1, 949],
        [100,   0,   0,   0,   0,   0,   1, 951],
        [100,   0,   0,   0,   0,   0,   2, 766],
        [100,   0,   0,   0,   0,   0,   2, 783],
        [100,   0,   0,   0,   0,   0,   2, 825],


In [14]:
print(get_e_by_dict(c_dict, 543))
print(get_e_by_dict(c_dict, 874))

<http://dbpedia.org/ontology/Province>
<http://www.w3.org/2002/07/owl#Thing>


In [ ]:
for x in train_dataloader:
    print(x)
    x_sub = torch.index_select(x, 0, (x[:, 0, 0] == 0).nonzero().squeeze(-1))
    print(x_sub)
    break

### 优化算法时间
3p: 100 55->33 200 80->45 300 102->50 400 119->52 500 137->54

In [12]:
start_time = time.time()
jaccards = []
for index, (pos, mix) in enumerate(loader):
    if index > 1000:
        break
    logits = model.predict(mix, query_type='2i', answer_type='e')
#     print(pos)
    er = (pos[0, 3].item(), pos[0, 4].item(), pos[0, 5].item(), pos[0, 6].item())
    filter_e = filters_e[er]
#     print("filter_e:" + str(filter_e))
    ranks = torch.argsort(logits.squeeze(dim=0), descending=True)
#     print(ranks[:34])
#     sims, targets, answers = valid(ranks.tolist(), 500, '3p', pos[0].tolist(), graph, model, 0.999)
    targets, answers = valid_optimize(ranks.tolist(), 500, '2i', pos[0].tolist(), graph, model, 0.80)
    print(er, ":", targets)
    print(er, ":", gt[er])
    rank = (ranks == (pos[0, -1])).nonzero().item() + 1
#     print("rank_before", rank)
    ranks_better = ranks[:rank - 1]
#     print("ranks_better:", ranks_better)
#     print("filter_e:", filter_e)
    for t in filter_e:
        if (ranks_better == t).sum() == 1:
            rank -= 1
    jaccards.append(jaccard_similarity(answers, gt[er]))
#     print(index, "rank_after:", rank) 
end_time = time.time()
run_time = end_time - start_time
print(run_time)
print(np.mean(jaccards))

(20481, 16, 12929, 17) : [(7069, 0.969)]
(20481, 16, 12929, 17) : [7069]
(17172, 145, 17172, 253) : [(17762, 0.946), (17763, 0.946), (3185, 0.946)]
(17172, 145, 17172, 253) : [17762, 17763]
(20952, 27, 27704, 27) : [(15414, 1.0)]
(20952, 27, 27704, 27) : [5766, 15414]
(18188, 27, 12386, 61) : []
(18188, 27, 12386, 61) : [14098]
(15535, 17, 12352, 16) : [(27592, 0.969), (26436, 0.969), (3662, 0.939)]
(15535, 17, 12352, 16) : [3662, 27592, 26436]
(14447, 160, 27065, 61) : []
(14447, 160, 27065, 61) : [4601]
(15811, 27, 16128, 27) : [(4197, 1.0)]
(15811, 27, 16128, 27) : [17447, 4197]
(16987, 323, 6317, 323) : []
(16987, 323, 6317, 323) : [7305]
(4042, 95, 20863, 95) : []
(4042, 95, 20863, 95) : [11924]
(21515, 161, 6034, 160) : [(27185, 0.876)]
(21515, 161, 6034, 160) : [27061]
(24474, 95, 21720, 95) : [(3789, 0.801)]
(24474, 95, 21720, 95) : [27341]
(6381, 100, 10765, 100) : [(15336, 1.0), (16876, 0.883)]
(6381, 100, 10765, 100) : [24590, 15336]
(21842, 152, 4973, 152) : []
(21842, 152,

(11682, 142, 14897, 142) : []
(11682, 142, 14897, 142) : [18874]
(18190, 189, 1014, 73) : [(7840, 0.824), (3225, 1.0), (24490, 0.824), (18412, 0.824), (8272, 0.824), (26389, 0.824), (27734, 0.824), (18777, 1.0), (10047, 1.0)]
(18190, 189, 1014, 73) : [18773, 3225, 18777, 10047]
(27463, 61, 3519, 61) : []
(27463, 61, 3519, 61) : [16192]
(17253, 6, 6016, 6) : []
(17253, 6, 6016, 6) : [28053]
(2188, 111, 28101, 111) : []
(2188, 111, 28101, 111) : [7815]
(20408, 297, 2968, 73) : [(16222, 0.919)]
(20408, 297, 2968, 73) : [8257]
(923, 137, 22447, 160) : []
(923, 137, 22447, 160) : [10175]
(16999, 137, 233, 137) : []
(16999, 137, 233, 137) : [4582]
(20777, 203, 25787, 135) : []
(20777, 203, 25787, 135) : [13173]
(27574, 307, 16597, 307) : [(12344, 1.0)]
(27574, 307, 16597, 307) : [9642, 12344]
(27815, 131, 13694, 132) : [(26645, 1.0)]
(27815, 131, 13694, 132) : [25775, 26645]
(6951, 61, 14868, 225) : []
(6951, 61, 14868, 225) : [11103]
(16194, 249, 5840, 249) : []
(16194, 249, 5840, 249) : [7

(7611, 152, 11986, 152) : []
(7611, 152, 11986, 152) : [27325]
(15178, 61, 15228, 61) : []
(15178, 61, 15228, 61) : [4420]
(13034, 27, 103, 61) : []
(13034, 27, 103, 61) : [11077]
(6074, 111, 27626, 111) : []
(6074, 111, 27626, 111) : [19442]
(24880, 78, 253, 249) : []
(24880, 78, 253, 249) : [24103]
(20967, 61, 9788, 160) : []
(20967, 61, 9788, 160) : [14098]
(5875, 137, 21617, 137) : []
(5875, 137, 21617, 137) : [6288]
(25899, 70, 329, 61) : [(23600, 0.949)]
(25899, 70, 329, 61) : [23600]
(21777, 210, 5779, 193) : []
(21777, 210, 5779, 193) : [12919]
(8819, 111, 21223, 111) : []
(8819, 111, 21223, 111) : [9561]
(9340, 27, 14421, 27) : []
(9340, 27, 14421, 27) : [10815]
(27279, 61, 21126, 225) : []
(27279, 61, 21126, 225) : [25962]
(27111, 56, 28092, 232) : []
(27111, 56, 28092, 232) : [28146]
(26021, 17, 26693, 16) : [(22102, 0.969)]
(26021, 17, 26693, 16) : [22102]
(21130, 208, 17435, 208) : [(20841, 1.0)]
(21130, 208, 17435, 208) : [3324, 20841]
(13290, 208, 3146, 208) : [(3789, 0.

(27433, 16, 23923, 16) : [(20952, 0.939), (23995, 0.939), (9587, 0.939), (22437, 0.939)]
(27433, 16, 23923, 16) : [9587, 20952, 23995, 22437]
(24887, 111, 7718, 111) : []
(24887, 111, 7718, 111) : [1456]
(2176, 61, 21742, 61) : []
(2176, 61, 21742, 61) : [13795]
(23713, 17, 14766, 17) : [(18253, 0.969), (14482, 1.0), (28117, 1.0), (27742, 1.0), (24507, 0.969), (8060, 1.0), (8764, 1.0)]
(23713, 17, 14766, 17) : [24507, 28117, 14482, 8764, 27742, 8060]
(16506, 17, 14704, 17) : [(22912, 0.969)]
(16506, 17, 14704, 17) : [22912]
(20559, 111, 3549, 111) : [(1413, 1.0), (1014, 1.0)]
(20559, 111, 3549, 111) : [18773, 1413, 1014]
(5352, 16, 9557, 17) : [(22035, 0.969), (5676, 0.939), (5495, 0.969)]
(5352, 16, 9557, 17) : [22035, 5495]
(15839, 111, 5430, 111) : [(16222, 1.0)]
(15839, 111, 5430, 111) : [1456, 16222]
(8749, 16, 22271, 16) : []
(8749, 16, 22271, 16) : [12898]
(18423, 257, 932, 257) : []
(18423, 257, 932, 257) : [28097]
(14801, 323, 8505, 27) : []
(14801, 323, 8505, 27) : [23455]
(1

(19880, 17, 19880, 16) : [(8277, 0.969), (21767, 0.969)]
(19880, 17, 19880, 16) : [21767, 8277]
(13486, 61, 16133, 229) : []
(13486, 61, 16133, 229) : [24889]
(9093, 307, 16053, 307) : [(26023, 0.852)]
(9093, 307, 16053, 307) : [26665]
(17288, 323, 9529, 124) : [(5422, 0.879)]
(17288, 323, 9529, 124) : [5422]
(10261, 27, 27773, 70) : []
(10261, 27, 27773, 70) : [13439]
(7104, 56, 15525, 301) : []
(7104, 56, 15525, 301) : [27639]
(14976, 16, 21301, 16) : [(9980, 0.939)]
(14976, 16, 21301, 16) : [9980]
(21195, 203, 21232, 240) : []
(21195, 203, 21232, 240) : [13482]
(19314, 295, 7077, 27) : []
(19314, 295, 7077, 27) : [25696]
(17634, 203, 13443, 203) : [(7845, 1.0)]
(17634, 203, 13443, 203) : [25244, 7845]
(24864, 17, 5676, 16) : [(9557, 0.969), (14326, 0.939)]
(24864, 17, 5676, 16) : [14326, 9557]
(24199, 16, 12518, 17) : [(16042, 0.969)]
(24199, 16, 12518, 17) : [16042]
(19459, 249, 24289, 249) : []
(19459, 249, 24289, 249) : [9328]
(13123, 225, 756, 70) : []
(13123, 225, 756, 70) : [1

(13186, 111, 18905, 297) : []
(13186, 111, 18905, 297) : [9561]
(2670, 217, 22142, 137) : []
(2670, 217, 22142, 137) : [17441]
(20131, 111, 12898, 111) : [(18000, 1.0), (3074, 1.0), (26508, 1.0), (28263, 1.0)]
(20131, 111, 12898, 111) : [7486, 3074, 18000, 26508, 28263]
(14148, 135, 18265, 135) : []
(14148, 135, 18265, 135) : [24669]
(26319, 249, 24018, 249) : []
(26319, 249, 24018, 249) : [23521]
(20554, 16, 18131, 100) : [(14614, 0.969)]
(20554, 16, 18131, 100) : [14614]
(9659, 27, 8591, 61) : []
(9659, 27, 8591, 61) : [26080]
(15220, 295, 4263, 50) : [(14098, 0.934)]
(15220, 295, 4263, 50) : [3900]
(23949, 249, 11376, 249) : []
(23949, 249, 11376, 249) : [26662]
(13450, 249, 9342, 249) : [(10388, 1.0)]
(13450, 249, 9342, 249) : [16007, 10388]
(24570, 27, 25196, 161) : [(23600, 0.876)]
(24570, 27, 25196, 161) : [3652]
(3992, 111, 27587, 111) : []
(3992, 111, 27587, 111) : [1014]
(24880, 77, 7694, 249) : []
(24880, 77, 7694, 249) : [24103]
(15564, 135, 6455, 135) : [(13173, 1.0)]
(155

(5112, 323, 19864, 240) : []
(5112, 323, 19864, 240) : [13257]
(17738, 17, 11202, 16) : [(7718, 0.939)]
(17738, 17, 11202, 16) : [7718]
(13627, 249, 21767, 249) : [(11327, 1.0)]
(13627, 249, 21767, 249) : [20203, 11327]
(13377, 249, 25554, 249) : []
(13377, 249, 25554, 249) : [9365]
(9587, 249, 21107, 249) : []
(9587, 249, 21107, 249) : [7613]
(10048, 17, 8106, 16) : [(15056, 0.969), (11375, 0.939)]
(10048, 17, 8106, 16) : [11375, 15056]
(3626, 323, 6821, 252) : [(4420, 0.879)]
(3626, 323, 6821, 252) : [4420]
(18784, 277, 21074, 277) : [(24232, 1.0), (23917, 1.0)]
(18784, 277, 21074, 277) : [24252, 23917, 24232]
(8483, 307, 6305, 307) : []
(8483, 307, 6305, 307) : [26740]
(14287, 237, 25853, 56) : [(14289, 1.0), (2877, 1.0), (2526, 0.877), (3005, 0.877)]
(14287, 237, 25853, 56) : [5619, 14289, 2877]
(15507, 17, 11407, 16) : [(7718, 0.939)]
(15507, 17, 11407, 16) : [7718]
(17464, 258, 19689, 295) : []
(17464, 258, 19689, 295) : [26243]
(15487, 16, 13230, 17) : [(26816, 0.969)]
(15487, 1

(14246, 111, 13965, 111) : []
(14246, 111, 13965, 111) : [12013]
(19616, 111, 21333, 111) : []
(19616, 111, 21333, 111) : [7030]
(3323, 111, 12119, 111) : []
(3323, 111, 12119, 111) : [25857]
(8315, 126, 13621, 27) : []
(8315, 126, 13621, 27) : [14098]
(5626, 301, 10926, 56) : []
(5626, 301, 10926, 56) : [26334]
(15535, 17, 21931, 17) : [(18001, 1.0), (4569, 1.0), (3662, 0.969)]
(15535, 17, 21931, 17) : [3662, 4569, 18001]
(6810, 137, 6798, 137) : [(6288, 1.0), (2842, 1.0)]
(6810, 137, 6798, 137) : [19575, 2842, 6288]
(19618, 137, 5897, 137) : []
(19618, 137, 5897, 137) : [6288]
(16183, 153, 21036, 231) : [(8037, 0.963)]
(16183, 153, 21036, 231) : [8037]
(17611, 111, 17456, 111) : [(20743, 1.0)]
(17611, 111, 17456, 111) : [17246, 20743]
(9153, 27, 14172, 27) : [(1696, 1.0)]
(9153, 27, 14172, 27) : [1958, 1696]
(10362, 27, 10968, 27) : [(2075, 1.0)]
(10362, 27, 10968, 27) : [2961, 2075]
(26631, 120, 5980, 61) : []
(26631, 120, 5980, 61) : [16740]
(18839, 295, 19494, 295) : [(14098, 0.87

(10638, 27, 17185, 27) : []
(10638, 27, 17185, 27) : [7870]
(11920, 69, 12830, 69) : []
(11920, 69, 12830, 69) : [2129]
(21833, 234, 17977, 150) : []
(21833, 234, 17977, 150) : [21843]
(24157, 225, 8651, 9) : []
(24157, 225, 8651, 9) : [23879]
(28457, 307, 24, 307) : [(12344, 1.0)]
(28457, 307, 24, 307) : [9642, 12344]
(17480, 111, 15160, 111) : []
(17480, 111, 15160, 111) : [4953]
(2929, 307, 10424, 307) : [(9642, 1.0)]
(2929, 307, 10424, 307) : [12344, 9642]
(10726, 17, 15332, 16) : [(27592, 0.969), (26286, 0.969), (18001, 0.969), (9619, 1.0), (9051, 0.939)]
(10726, 17, 15332, 16) : [9051, 9619, 27592, 26286, 18001]
(3873, 50, 6663, 61) : []
(3873, 50, 6663, 61) : [15293]
(13661, 17, 17596, 17) : [(14192, 0.969)]
(13661, 17, 17596, 17) : [14192]
(15809, 160, 8260, 126) : []
(15809, 160, 8260, 126) : [71]
(15174, 17, 6381, 16) : [(24834, 0.939)]
(15174, 17, 6381, 16) : [24834]
(24569, 165, 17068, 132) : []
(24569, 165, 17068, 132) : [23996]
(5847, 21, 21518, 16) : []
(5847, 21, 21518,

In [14]:
graph[26323]

AtlasView({9088: {'relation': '<http://wikidata.dbpedia.org/ontology/season>', 'r_dict': 269}})

In [20]:
pos = torch.tensor([[11, 0, 0, 0, 0, 2,   307, 12344]])
torch.index_select(pos, 0, (pos[:, 0, 0] == 11).nonzero().squeeze(-1))

IndexError: too many indices for tensor of dimension 2

575 111 </br>
不存在 14525 28285 26792 </br>
存在 [26508, 12689, 16222, 6237, 12744, 3074, 28263, 26714] </br>

In [12]:
paths = nx.all_simple_paths(graph, 9343, 10026, 3)
for i in paths:
    print(i)

[9343, 26365, 26476, 10026]
[9343, 26476, 13994, 10026]
[9343, 26476, 25398, 10026]
[9343, 26476, 8723, 10026]
[9343, 26476, 10026]
[9343, 26476, 25646, 10026]


In [17]:
print(graph[3][6716])
print(graph[6716][26508])
print(graph[26508][11459])
print(cos_sim(model, 239, 190))
print(cos_sim(model, 111, 111))
print(cos_sim(model, 111, 297))

{'relation': '<http://wikidata.dbpedia.org/ontology/associatedMusicalArtist>', 'r_dict': 17}
{'relation': '<http://wikidata.dbpedia.org/ontology/genre>', 'r_dict': 111}
{'relation': '<http://wikidata.dbpedia.org/ontology/stylisticOrigin>', 'r_dict': 297}
0.812
1.0
0.87


In [20]:
get_e_by_dict(e_dict, 839)

'<http://wikidata.dbpedia.org/ontology/PopulatedPlace>'

In [16]:
graph[294][15844]

{'relation': '<http://wikidata.dbpedia.org/ontology/producer>', 'r_dict': 239}

In [11]:
graph[22446]

AtlasView({12518: {'relation': '<http://wikidata.dbpedia.org/ontology/associatedMusicalArtist>', 'r_dict': 17}, 18197: {'relation': '<http://wikidata.dbpedia.org/ontology/associatedMusicalArtist>', 'r_dict': 17}, 4197: {'relation': '<http://wikidata.dbpedia.org/ontology/birthPlace>', 'r_dict': 27}, 14098: {'relation': '<http://wikidata.dbpedia.org/ontology/birthPlace>', 'r_dict': 27}, 16300: {'relation': '<http://wikidata.dbpedia.org/ontology/birthPlace>', 'r_dict': 27}, 22446: {'relation': '<http://wikidata.dbpedia.org/ontology/deathPlace>', 'r_dict': 70}, 10061: {'relation': '<http://wikidata.dbpedia.org/ontology/genre>', 'r_dict': 111}, 25857: {'relation': '<http://wikidata.dbpedia.org/ontology/genre>', 'r_dict': 111}, 4292: {'relation': '<http://wikidata.dbpedia.org/ontology/instrument>', 'r_dict': 135}, 4629: {'relation': '<http://wikidata.dbpedia.org/ontology/instrument>', 'r_dict': 135}, 17719: {'relation': '<http://wikidata.dbpedia.org/ontology/instrument>', 'r_dict': 135}, 161